## Prueba 4
#### Desarrollar un sistema de eventos discretos para EMOV utilizando Simpy.

In [1]:
#Se importan las librerias
import simpy
import random
import matplotlib.pyplot as plt

In [11]:
CARRILES = 3
CARRIL_PESADOS = 1
CARRIL_NORMAL = 2
CARROS = ['Normal', 'Gran Tonelaje']

TP_REVISION = 20 #min
TP_FALLA = 2880 #2 dias
TIEMPO_SIMULACION = 43200 #30 dias

libres = []

def tiempo_falla():
    return random.expovariate(1/TP_FALLA)

def tiempo_revision():
    return random.normalvariate(TP_REVISION, 10)

class Cuenca_aire(object):
    def __init__(self, environment, num_carriles):
        # Guardamos como variable el entorno de ejecucion
        self.env=environment
        # Creamos el recurso que representa los carriles
        self.carriles = simpy.Resource(environment, num_carriles)
        self.falla = False
        
    def revisar_vehiculo(self, vehiculo):
        while True:
            demora_revision = tiempo_revision()
            try:
                inicio = self.env.now
                if "normal" in vehiculo:

                    print('Revision completada vehículo normal')
                elif "grande" in vehiculo:
                    print('Revision completada vehículo de gran tonelaje')
            
            except:
                self.falla = True
                

    def notificar_arreglo(self):
        while True:
            yield self.env.timeout(tiempo_falla()) # Generar  el tiempo de arreglo
            if not self.falla: # Mientras no se arregle sigue esperando 
                self.proceso.interrupt() 

def llegada_vehiculo(env, tipo, emov):
    #Estacionamiento
    yield env.timeout(random.randint(3,5))
    print('Llega a estacionarse: %s en el minuto %.2f.' % (tipo, env.now))
    #Sacar turno
    yield env.timeout(random.randint(1,3))
    print('Saca el turno: %s en el minuto %.2f.' % (tipo, env.now))
    #Pagar matricula
    yield env.timeout(random.randint(5,10))
    print('Paga la matricula: %s en el minuto %.2f.' % (tipo, env.now))

    with emov.carriles.request() as carril:
        # Ocupamos el carril de revision
        yield carril
        # Indicamos que vehiculo entra a la revision
        if tipo == 'Normal':
            print('En revision: %s en el minuto %.2f en el Carril %s.' % (tipo, env.now, 1))
            # Procesamos la revision
            yield env.process(emov.revisar_vehiculo(tipo))
            # Una vez que termina la llamada con 'yield', se indica que se ha lavado el vehiculo
            print('Vehículo [%s] revisado a las %.2f en el Carril %s.' % (tipo, env.now, 1))
        
        if tipo == "Gran Tonelaje":
            print('En revision: %s en el minuto %.2f en el Carril %s.' % (tipo, env.now, 3))
            # Procesamos la revision
            yield env.process(emov.revisar_vehiculo(tipo))
            # Una vez que termina la llamada con 'yield', se indica que se ha lavado el vehiculo
            print('Vehículo [%s] revisado a las %.2f en el Carril %s.' % (tipo, env.now, 1))

def salida_vehiculo(env, tipo):
    #Pegar sello
    yield env.timeout(random.randint(1,3))
    #Salir
    yield env.timeout(random.randint(5,10))

def generar_auto():
    num = random.randint(0,1)
    return CARROS[num]

def ejecutar_simulacion(env, num_carriles):
    emov = Cuenca_aire(env, num_carriles)
    
    # Creamos 5 llegadas de vehiculos iniciales
    for i in range(5):                      
        env.process(llegada_vehiculo(env, str(generar_auto())+'-%d'%(i+1),emov))
    
    # Ejecutamos la simulacion
    while True:                  
        yield env.timeout(random.randint(1,2))
        i+=1
        # Mientras se revisan los vehiculos, generamos mas vehiculos
        env.process(llegada_vehiculo(env,str(generar_auto())+'-%d'%(i+1),emov))

print('EMOV Cuenca-aire')
# Inicializamos la semilla aleatoria
random.seed(77)

# Creamos el entorno de simulacion
env=simpy.Environment()
env.process(ejecutar_simulacion(env, CARRILES))

# Ejecutamos el proceso durante el tiempo de simulacion
env.run(until = TIEMPO_SIMULACION)


EMOV Cuenca-aire
Llega a estacionarse: Normal-5 en el minuto 3.00.
Llega a estacionarse: Gran Tonelaje-1 en el minuto 4.00.
Llega a estacionarse: Gran Tonelaje-2 en el minuto 4.00.
Saca el turno: Normal-5 en el minuto 4.00.
Llega a estacionarse: Normal-3 en el minuto 5.00.
Llega a estacionarse: Normal-4 en el minuto 5.00.
Llega a estacionarse: Normal-6 en el minuto 5.00.
Llega a estacionarse: Normal-7 en el minuto 5.00.
Saca el turno: Gran Tonelaje-2 en el minuto 6.00.
Saca el turno: Normal-3 en el minuto 6.00.
Saca el turno: Gran Tonelaje-1 en el minuto 7.00.
Saca el turno: Normal-6 en el minuto 7.00.
Llega a estacionarse: Normal-8 en el minuto 8.00.
Saca el turno: Normal-4 en el minuto 8.00.
Saca el turno: Normal-7 en el minuto 8.00.
Paga la matricula: Normal-5 en el minuto 9.00.
Llega a estacionarse: Normal-9 en el minuto 9.00.
Llega a estacionarse: Gran Tonelaje-10 en el minuto 10.00.
Paga la matricula: Normal-3 en el minuto 11.00.
Saca el turno: Normal-8 en el minuto 11.00.
Llega 